In [1]:
import requests
import pandas as pd
from datetime import datetime
from tqdm import tqdm

BINANCE_CANDLE_COLUMNS = ['opentime', 'openprice', 'highprice', 'lowprice', 'closeprice', 'volume', 'closetime',
                          'quotevolume', 'trades', 'taker_buy_volume', 'taker_buy_quote', 'unused']

def binance_recursive_fetch_2(coins, interval, starttime, endtime, data_type='spot'):
    all_coins_result = {}
    data_list = []
    call_dict = {}
    
    for coin in tqdm(coins):
        result_list = []
        current_time = starttime
        call = 0
        timestamps = []
        
        while current_time < endtime:
            if ((int((endtime - current_time) / (1000 * 60))) + 1) >= 1000:
                limit = 1000
            else:
                limit = int((endtime - current_time) / (1000 * 60) + 1)
            
            if data_type == 'spot':
                url = (f'https://api.binance.com/api/v3/klines'
                       f'?symbol={coin}USDT'
                       f'&startTime={str(current_time)}'
                       f'&interval={interval}'
                       f'&limit={str(limit)}')
            elif data_type == 'futures':
                url = (f'https://fapi.binance.com/fapi/v1/klines'
                       f'?symbol={coin}USDT'
                       f'&startTime={str(current_time)}'
                       f'&interval={interval}'
                       f'&limit={str(limit)}')
            
            result_list += requests.get(url).json()
            
            if result_list:
                # Update current_time with the timestamp of the last data point fetched, plus 1 minute (60000 ms)
                current_time = result_list[-1][0] + 60000
                timestamps.append(current_time)
                call += 1
                
                # Check if the last fetched timestamp is greater than or equal to endtime
                if current_time >= endtime:
                    print(f"Reached endtime at {datetime.fromtimestamp(current_time / 1000).strftime('%Y-%m-%d %H:%M:%S')}. Stopping fetch.")
                    break
                
                print((datetime.fromtimestamp(current_time / 1000).strftime('%Y-%m-%d %H:%M:%S')) + 
                      f' status : {current_time < endtime}, time : {current_time}, limit : {call * 2}')
            
            # Ensure there's no continuous fetching of the same timestamp
            if len(timestamps) > 1 and timestamps[-1] == timestamps[-2]:
                print("Duplicate timestamp detected. Stopping fetch.")
                break
            
            # Sleep if needed to avoid rate limiting (adjust based on your rate limit)
            # time.sleep(0.1)  # Uncomment if needed
            
        current_df = pd.DataFrame(result_list, columns=BINANCE_CANDLE_COLUMNS)
        current_df['coin'] = coin
        current_df = current_df[['coin'] + BINANCE_CANDLE_COLUMNS]
        current_df = current_df.values.tolist()
        
        data_list += current_df
        call_dict.update({coin: call})
    
    return {'data': data_list, 'call': call_dict}

# Set endtime to the current time (today)
endtime = int(datetime.utcnow().timestamp() * 1000)

# # Example usage with today's date as the end time
# sample_spot = binance_recursive_fetch_2(
#     ['USDT'],
#     '1m',
#     starttime=int(pd.to_datetime('2023-01-01 00:00', utc=True).timestamp() * 1000),
#     endtime=endtime,
#     data_type='spot'  # Fetch spot data
# )

# print(sample_spot['data'])

/tmp/ipykernel_1101796/3312417040.py:74: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  endtime = int(datetime.utcnow().timestamp() * 1000)


In [4]:
# Fetch NEAR USDT
sample = binance_recursive_fetch_2(
    ['SUI'],
    '15m',
    starttime=int(pd.to_datetime('2000-01-01 00:00', utc=True).timestamp() * 1000),
    endtime=endtime,
    data_type='futures'  # Fetch spot/futures data
)

print(sample['data'])

  0%|          | 0/1 [00:00<?, ?it/s]

2023-05-14 01:46:00 status : True, time : 1684028760000, limit : 2
2023-05-24 11:46:00 status : True, time : 1684928760000, limit : 4
2023-06-03 21:46:00 status : True, time : 1685828760000, limit : 6
2023-06-14 07:46:00 status : True, time : 1686728760000, limit : 8
2023-06-24 17:46:00 status : True, time : 1687628760000, limit : 10
2023-07-05 03:46:00 status : True, time : 1688528760000, limit : 12
2023-07-15 13:46:00 status : True, time : 1689428760000, limit : 14
2023-07-25 23:46:00 status : True, time : 1690328760000, limit : 16
2023-08-05 09:46:00 status : True, time : 1691228760000, limit : 18
2023-08-15 19:46:00 status : True, time : 1692128760000, limit : 20
2023-08-26 05:46:00 status : True, time : 1693028760000, limit : 22
2023-09-05 15:46:00 status : True, time : 1693928760000, limit : 24
2023-09-16 01:46:00 status : True, time : 1694828760000, limit : 26
2023-09-26 11:46:00 status : True, time : 1695728760000, limit : 28
2023-10-06 21:46:00 status : True, time : 1696628760

100%|██████████| 1/1 [00:06<00:00,  6.79s/it]

[['SUI', 1683129600000, '1.403000', '1.403000', '1.265200', '1.333800', '11474534.0', 1683130499999, '15172173.0999100', 43648, '5505355.7', '7277550.4421300', '0'], ['SUI', 1683130500000, '1.333900', '1.386300', '1.332700', '1.371600', '16090260.4', 1683131399999, '21971036.3647800', 72866, '8103409.6', '11068069.4296900', '0'], ['SUI', 1683131400000, '1.371700', '1.395700', '1.354700', '1.385700', '13192974.2', 1683132299999, '18205088.6870900', 57805, '6829156.6', '9423169.0121800', '0'], ['SUI', 1683132300000, '1.386600', '1.392400', '1.365200', '1.373300', '11951258.0', 1683133199999, '16469710.6071200', 46428, '5673737.9', '7822082.9110000', '0'], ['SUI', 1683133200000, '1.373100', '1.375600', '1.340500', '1.357400', '12698235.4', 1683134099999, '17197298.6656000', 50735, '6035706.0', '8176917.2019800', '0'], ['SUI', 1683134100000, '1.357000', '1.392800', '1.354000', '1.382000', '9232800.2', 1683134999999, '12724157.4965500', 40901, '4840829.3', '6669670.2298800', '0'], ['SUI', 1

In [5]:
# Define the column names for the DataFrame based on the Binance API response structure
columns = ['coin', 'opentime', 'openprice', 'highprice', 'lowprice', 'closeprice', 'volume', 'closetime', 
           'quotevolume', 'trades', 'taker_buy_volume', 'taker_buy_quote', 'unused']

# Convert the list of data into a DataFrame
df = pd.DataFrame(sample['data'], columns=columns)

# Show the first few rows of the DataFrame
df

coin       opentime openprice highprice  lowprice closeprice  \
0      SUI  1683129600000  1.403000  1.403000  1.265200   1.333800   
1      SUI  1683130500000  1.333900  1.386300  1.332700   1.371600   
2      SUI  1683131400000  1.371700  1.395700  1.354700   1.385700   
3      SUI  1683132300000  1.386600  1.392400  1.365200   1.373300   
4      SUI  1683133200000  1.373100  1.375600  1.340500   1.357400   
...    ...            ...       ...       ...       ...        ...   
58323  SUI  1735620300000  4.078700  4.085000  4.061600   4.082800   
58324  SUI  1735621200000  4.082900  4.095300  4.073800   4.081000   
58325  SUI  1735622100000  4.081100  4.099000  4.063700   4.098200   
58326  SUI  1735623000000  4.098200  4.131000  4.090000   4.119800   
58327  SUI  1735623900000  4.119900  4.129300  4.106100   4.119100   

           volume      closetime       quotevolume  trades taker_buy_volume  \
0      11474534.0  1683130499999  15172173.0999100   43648        5505355.7   
1      16090260.4  1683131399999  21971036.3647800   72866        8103409.6   
2      13192974.2  1683132299999  18205088.6870900   57805        6829156.6   
3      11951258.0  1683133199999  16469710.6071200   46428        5673737.9   
4      12698235.4  1683134099999  17197298.6656000   50735        6035706.0   
...           ...            ...               ...     ...              ...   
58323   1863281.5  1735621199999   7589594.7539500   20948         927866.5   
58324    854988.6  1735622099999   3493640.1315900   13288         392507.9   
58325   1221874.8  1735622999999   4985167.0770400   18433         781802.8   
58326   1702835.3  1735623899999   7003625.4318500   26801         850966.2   
58327    625389.3  1735624799999   2575282.0221700   13212         274271.4   

        taker_buy_quote unused  
0       7277550.4421300      0  
1      11068069.4296900      0  
2       9423169.0121800      0  
3       7822082.9110000      0  
4       8176917.2019800      0  
...                 ...    ...  
58323   3779383.4110900      0  
58324   1603318.4795100      0  
58325   3190057.2480600      0  
58326   3498465.4542300      0  
58327   1129335.2655900      0  

[58328 rows x 13 columns]

In [6]:
df.to_csv('SUI_USDT_futures_15m_20241231.csv', index=False)

print("DataFrame has been saved to csv")

DataFrame has been saved to csv
